In [43]:
from numpy import *
from numpy.linalg import norm
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot, plot
init_notebook_mode(connected=True)
%matplotlib inline

In [2]:
# Sphere settings
RADIUS = 15
LINES = 120
RESOLUTION = 120

# Subspace settings
SIDE = RADIUS / 300

# Axes settings
AXES_LEN = RADIUS

# Problem settings
SCALE = 1
CITIES = {
    'melbourne': (-37.8140000, 144.9633200),
    'sydney': (-33.8678500, 151.2073200),
    'perth': (-31.9522400, 115.8614000),
    'san francisco': (37.773972, -122.431297),
    'new york': (40.730610, -73.935242),
    'washington': (38.8951100, -77.0363700),
    'austin': (30.2671500, -97.7430600)
}
CITY1, CITY2 = 'new york', 'austin'

In [80]:
def subspace(transf_matrix):
    def gen_points(points, transf_matrix):
        points = transf_matrix @ points
        line_params = {'mode': 'lines', 'showlegend': False, 'line': go.Line(color='#999', width=2)}
        return go.Scatter3d(x=points[0,:], y=points[1,:], z=points[2,:], **line_params)
        
    city1 = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY1][1]), RADIUS)
    city2 = polar_to_cartesian(deg2rad(CITIES[CITY2][0]), deg2rad(CITIES[CITY2][1]), RADIUS)
    city1 = list(city1) + [1]
    city2 = list(city2) + [1]
    x_span, y_span, _, _ = abs(transf_matrix.T @ city1 - transf_matrix.T @ city2)
    x_span = arange(-x_span/2, +x_span/2, SIDE)
    y_span = arange(-y_span/2, +y_span/2, SIDE)
    
    xv, yv = meshgrid(x_span, y_span)
    zv = zeros_like(xv)
    tv = ones_like(xv)
    traces = []
    for x, y, z, t in zip(xv, yv, zv, tv):
        points = vstack([x, y, z, t])
        traces.append(gen_points(points, transf_matrix))
    for x, y, z, t in zip(xv.T, yv.T, zv.T, tv.T):
        points = vstack([x.T, y.T, z.T, t.T])
        traces.append(gen_points(points, transf_matrix))
    
    return traces

def wg84_axes():
    return axes(identity(4))

def subspace_axes(transf_matrix):
    return axes(transf_matrix)

def axes(transf_matrix):
    traces = []
    line_params = {'mode': 'lines', 'showlegend': False}
    points = transf_matrix @ array([[0,0,0,1],[AXES_LEN,0,0,1]]).T
    traces.append(go.Scatter3d(x=points[0,:], y=points[1,:], z=points[2,:], name='X', line=go.Line(color='#F00', width=3), **line_params))
    points = transf_matrix @ array([[0,0,0,1],[0,AXES_LEN,0,1]]).T
    traces.append(go.Scatter3d(x=points[0,:], y=points[1,:], z=points[2,:], name='Y', line=go.Line(color='#0F0', width=3), **line_params))
    points = transf_matrix @ array([[0,0,0,1],[0,0,AXES_LEN,1]]).T
    traces.append(go.Scatter3d(x=points[0,:], y=points[1,:], z=points[2,:], name='Z', line=go.Line(color='#00F', width=3), **line_params))
    return traces

def cities():
    traces = []
    city1 = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY1][1]), RADIUS)
    city2 = polar_to_cartesian(deg2rad(CITIES[CITY2][0]), deg2rad(CITIES[CITY2][1]), RADIUS)
    traces.append(go.Scatter3d(x=city1[0:1], y=city1[1:2], z=city1[2:3], mode='markers', marker=go.Marker(size=4), name=CITY1.title()))
    traces.append(go.Scatter3d(x=city2[0:1], y=city2[1:2], z=city2[2:3], mode='markers', marker=go.Marker(size=4), name=CITY2.title()))
    return traces

def polar_to_cartesian(lat, lon, alt):
    x = alt * cos(lat) * cos(lon)
    y = alt * cos(lat) * sin(lon)
    z = alt * sin(lat)
    return array([x, y, z])

def sphere():
    step = RESOLUTION // LINES
    theta = linspace(0, 2*pi, RESOLUTION)
    phi = linspace(0, pi, RESOLUTION)
    x = RADIUS * outer(cos(theta),sin(phi))
    y = RADIUS * outer(sin(theta),sin(phi))
    z = RADIUS * outer(ones(RESOLUTION),cos(phi))


    line_params = {'mode': 'lines', 'showlegend': False, 'line': go.Line(color='#CCC', width=2)}
    lon_lines, lat_lines = [], []
    for i in arange(0, x.shape[-1], step):
        lon_lines.append(go.Scatter3d(x=x[i,:], y=y[i,:], z=z[i,:], **line_params))
        lat_lines.append(go.Scatter3d(x=x[:,i], y=y[:,i], z=z[:,i], **line_params))
    
    return lon_lines + lat_lines

In [81]:
def plot_all(transf_matrix, extra_points=[]):
    data = go.Data(
        sphere() +
        wg84_axes() +
        subspace(transf_matrix) +
        subspace_axes(transf_matrix) +
        cities() + 
        [
            go.Scatter3d(x=[p[0]], y=[p[1]], z=[p[2]], mode='markers', marker=go.Marker(size=4))
            for p in extra_points
        ]
    )
    
    a = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY1][1]), RADIUS)
    b = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY2][1]), RADIUS)
    m = (a + b) / 2
    m = m / norm(m) * 2
    
    camera = dict(
        up=dict(x=0, y=0, z=1),
        center=dict(x=0, y=0, z=0),
        eye=dict(x=m[0], y=m[1], z=m[2])
    )
    layout = go.Layout(
        scene=go.Scene(camera=camera),
        title='World and local spaces',
        autosize=False,
        width=1000,
        height=1000,
        margin=go.Margin(l=65, r=50, b=65, t=90)
    )
    fig = go.Figure(data=data, layout=layout)
    iplot(fig)

In [82]:
transf_matrix = identity(4)
transf_matrix[(0,1,2),(0,1,2)] = SCALE
M_scaling = transf_matrix

In [83]:
transf_matrix = identity(4)
a = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY1][1]), RADIUS)
b = polar_to_cartesian(deg2rad(CITIES[CITY1][0]), deg2rad(CITIES[CITY2][1]), RADIUS)
c = polar_to_cartesian(deg2rad(CITIES[CITY2][0]), deg2rad(CITIES[CITY2][1]), RADIUS)
# d = polar_to_cartesian(deg2rad(CITIES[CITY2][0]), deg2rad(CITIES[CITY1][1]), RADIUS)
m = (a + c) / 2

# Base vector pointing outwards
e_3 = m / norm(m)
# Base vector parallel to the line connecting city1 to city2
e_1 = (b - a) / norm(b - a)
# Base vector perpendicular to the other two
e_2 = cross(e_3, e_1)

transf_matrix[(0,1,2),(0,0,0)] = e_1
transf_matrix[(0,1,2),(1,1,1)] = e_2
transf_matrix[(0,1,2),(2,2,2)] = e_3
M_rotation = transf_matrix

In [84]:
transf_matrix = identity(4)
z_offset = ((M_scaling @ M_rotation).T @ (list(c) + [1]))[2]
transf_matrix[2,3] = RADIUS / SCALE + (z_offset - RADIUS)
M_translation = transf_matrix

In [86]:
lat = CITIES[CITY1][0] * 2/3 + CITIES[CITY2][0] * 1/3
lon = CITIES[CITY1][1] * 2/3 + CITIES[CITY2][1] * 1/3
p = polar_to_cartesian(deg2rad(lat), deg2rad(lon), RADIUS)

T = M_scaling @ M_rotation @ M_translation
d = norm(T[(0,1,2),(3,3,3)]) # Distance from the origin to the plane
n = T[(0,1,2),(2,2,2)] / norm(T[(0,1,2),(2,2,2)]) # Normal of the plane (a.k.a. e_3)
pj = p - (norm(n @ p) - d) * n

plot_all(M_scaling @ M_rotation @ M_translation, [p, pj])